In [1]:
!git clone https://github.com/mueedurrehman/distiller.git
%cd distiller
!pip3 install -e .

Cloning into 'distiller'...
remote: Enumerating objects: 11, done.
remote: Counting objects: 100% (11/11), done.
remote: Compressing objects: 100% (7/7), done.
remote: Total 6174 (delta 4), reused 6 (delta 4), pack-reused 6163
Receiving objects: 100% (6174/6174), 39.83 MiB | 31.89 MiB/s, done.
Resolving deltas: 100% (4327/4327), done.
/content/distiller
Obtaining file:///content/distiller
     |████████████████████████████████| 2.1MB 21.1MB/s 
     |████████████████████████████████| 734.6MB 24kB/s 
     |████████████████████████████████| 10.2MB 144kB/s 
     |████████████████████████████████| 460kB 54.0MB/s 
     |████████████████████████████████| 110.5MB 45kB/s 
     |████████████████████████████████| 51kB 8.3MB/s 
     |████████████████████████████████| 798kB 47.1MB/s 
     |████████████████████████████████| 112kB 40.6MB/s 
     |████████████████████████████████| 1.7MB 51.0MB/s 
     |████████████████████████████████| 235kB 57.9MB/s 
     |████████████████████████████████| 153kB 55.0

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
import torch
import torchvision
import torchvision.transforms as transforms
import torchvision.models as models
from torchsummary import summary
import matplotlib.pyplot as plt
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import time
import math
import yaml
import distiller
from collections import OrderedDict
import os
import pandas as pd

In [3]:
!cp "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Baseline Models/baseResnet56" .
# !cp ../../../drive/MyDrive/CS6787\ -\ Final\ Project/Google\ Colab\ Scripts/Quantization\ Models/Resnet56\ Quantization\ Stats/resnet56_quant_stats.yaml .

Asymmetric U

In [4]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/4bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=none --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  109.28847 |   63.83257 |   63.83257 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    1.15427 |   -6.96875 |    6.96875 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    0.04471 |   -0.00244 |    0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          28478 |    0.00000 |    0.00000 |  1.56250 |  2.12402 |  0.00000 |   22.74848 |    0.04511 |   -0.00248 |    0.03276 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 1, 1)  |    

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/6bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=none --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |   459.14932 |  268.11078 |  268.11078 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |     4.84479 |  -29.35938 |   29.35938 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |     0.04471 |   -0.00243 |    0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          34370 |    0.00000 |    0.00000 |  0.00000 |  1.51367 |  0.00000 |    6.76541 |     0.04474 |   -0.00243 |    0.03314 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 1, 1)  |

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/8bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=none --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  1857.68811 |  1085.08972 |  1085.08972 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    19.29917 |  -118.95312 |   118.95312 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |     0.04471 |    -0.00243 |     0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          36027 |    0.00000 |    0.00000 |  0.00000 |  0.19531 |  0.00000 |    2.27051 |     0.04471 |    -0.00243 |     0.03317 |
| 174 | module.layer3.2.conv1.weight_scale             | (64, 1, 

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/10bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=none --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  29847.62109 |  17427.08203 |  17427.08203 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    309.71091 |  -1910.45312 |   1910.45312 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |      0.04471 |     -0.00243 |      0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          36813 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.13835 |      0.04471 |     -0.00243 |      0.03317 |
| 174 | module.layer3.2.conv1.weight_scale           

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/12bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=none --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  29844.10547 |  17426.70117 |  17426.70117 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    309.77060 |  -1910.42188 |   1910.42188 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |      0.04471 |     -0.00243 |      0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          36814 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.13563 |      0.04471 |     -0.00243 |      0.03317 |
| 174 | module.layer3.2.conv1.weight_scale           

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/14bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=none --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Streaming output truncated to the last 5000 lines.
| 170 | module.layer3.1.conv2.weight_scale             | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |  119471.94531 |   69728.72656 |   69728.72656 |
| 171 | module.layer3.1.conv2.weight_zero_point        | (64, 1, 1, 1)  |            64 |             64 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |    1239.26135 |   -7642.92188 |    7642.92188 |
| 172 | module.layer3.2.conv1.float_weight             | (64, 64, 3, 3) |         36864 |          36864 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.00000 |       0.04471 |      -0.00243 |       0.03317 |
| 173 | module.layer3.2.conv1.weight                   | (64, 64, 3, 3) |         36864 |          36847 |    0.00000 |    0.00000 |  0.00000 |  0.00000 |  0.00000 |    0.04612 |       0.04471 |      -0.00243 |       0.03317 |
| 174 | module.layer3.2.conv1.weight_scal

In [ ]:
!python3 /content/distiller/examples/classifier_compression/compress_classifier.py -a resnet56_cifar --compress="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QA/Asymmetric/16bitAsymmetricUQA.yaml" ./data --resume=baseResnet56 -o "/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone" --qe-stats-file="/content/drive/MyDrive/Colab Notebooks/6787 Notebooks/Google Colab Scripts/Schedules/Quantization Schedules/acts_quantization_stats.yaml" --qe-clip-acts=none --epochs 25 --vs=0 --lr=0.0001 --prioritizeAccuracy

Log file for this run: /content/drive/.shortcut-targets-by-id/14_4ehU2lLHHu6HAFmEenl_iXGrCYtNmi/Google Colab Scripts/Schedules/Quantization Schedules/QAResultsANone/2020.12.09-012337/2020.12.09-012337.log
Random seed: 95064

--------------------------------------------------------
Logging to TensorBoard - remember to execute the server:
> tensorboard --logdir='./logs'

=> created a resnet56_cifar model with the cifar10 dataset
The "--resume" flag is deprecated. Please use "--resume-from=YOUR_PATH" instead.
If you wish to also reset the optimizer, call with: --reset-optimizer
=> loading checkpoint baseResnet56
=> Checkpoint contents:
+----------------------+--------+----------------+
| Key                  | Type   | Value          |
|----------------------+--------+----------------|
| arch                 | str    | resnet56_cifar |
| compression_sched    | dict   |                |
| dataset              | str    | cifar10        |
| epoch                | int    | 127            |
| 